## Bash: First time executing

In [12]:
!pip3 install -q cython pyyaml==5.1
!git clone https://github.com/facebookresearch/detectron2 detectron2_repo
!pip3 install -q -e detectron2_repo
!pip3 install -q -U watermark
!pip3 install seaborn

You should consider upgrading via the 'C:\Users\Usuario\AppData\Local\Microsoft\WindowsApps\PythonSoftwareFoundation.Python.3.9_qbz5n2kfra8p0\python.exe -m pip install --upgrade pip' command.
Cloning into 'detectron2_repo'...
Updating files:  93% (706/758)
Updating files:  94% (713/758)
Updating files:  95% (721/758)
Updating files:  96% (728/758)
Updating files:  97% (736/758)
Updating files:  98% (743/758)
Updating files:  99% (751/758)
Updating files: 100% (758/758)
Updating files: 100% (758/758), done.
You should consider upgrading via the 'C:\Users\Usuario\AppData\Local\Microsoft\WindowsApps\PythonSoftwareFoundation.Python.3.9_qbz5n2kfra8p0\python.exe -m pip install --upgrade pip' command.
You should consider upgrading via the 'C:\Users\Usuario\AppData\Local\Microsoft\WindowsApps\PythonSoftwareFoundation.Python.3.9_qbz5n2kfra8p0\python.exe -m pip install --upgrade pip' command.


In [1]:
import os 
os.chdir('detectron2_repo')

In [2]:
import torch, torchvision
import detectron2
from detectron2.utils.logger import setup_logger
setup_logger()
import glob
import os
import ntpath
import numpy as np
import cv2
import random
import itertools
import pandas as pd
from tqdm import tqdm
import urllib
import json
import PIL.Image as Image
from detectron2 import model_zoo
from detectron2.engine import DefaultPredictor, DefaultTrainer
from detectron2.config import get_cfg
from detectron2.utils.visualizer import Visualizer, ColorMode
from detectron2.data import DatasetCatalog, MetadataCatalog, build_detection_test_loader
from detectron2.evaluation import COCOEvaluator, inference_on_dataset
from detectron2.structures import BoxMode
import seaborn as sns
from pylab import rcParams
import matplotlib.pyplot as plt
from matplotlib import rc
%matplotlib inline
%config InlineBackend.figure_format='retina'
sns.set(style='whitegrid', palette='muted', font_scale=1.2)
HAPPY_COLORS_PALETTE = ["#01BEFE", "#FFDD00", "#FF7D00", "#FF006D", "#ADFF02", "#8F00FF"]
sns.set_palette(sns.color_palette(HAPPY_COLORS_PALETTE))
rcParams['figure.figsize'] = 12, 8
RANDOM_SEED = 42
np.random.seed(RANDOM_SEED)
torch.manual_seed(RANDOM_SEED)


In [3]:
!gdown --id 1K79wJgmPTWamqb04Op2GxW0SW9oxw8KSç

"gdown" no se reconoce como un comando interno o externo,
programa o archivo por lotes ejecutable.


In [4]:
faces_df = pd.read_json('face_detection.json', lines=True)


In [3]:
folds = {}
i_ = -1
# <major_axis_radius minor_axis_radius angle center_x center_y detection_score>.

PATH = "FDDB-folds/"
for element in os.listdir(PATH):
    if 'ellipse' in element:
        i_ += 1
        folds[i_] = []
        with open(PATH + element,'r') as hdlr:
            lines = hdlr.readlines()
            for line in range(len(lines)):
                if '/' in lines[line]: 
                    new_image = [[],[]]
                    #print(lines[line]+ '.jpg')
                    
                    new_image[0] = cv2.imread(lines[line][:-1]+ '.jpg') 
                    for element in range(int(lines[line + 1])):
                        #print(lines[line + 2 + element][:-1].split(' '))
                        true = list(map(lambda x: float(x) , filter(lambda x: len(x) >0 ,lines[line + 2 + element][:-1].split(' '))))
                        xmin,xmax  = true[3] - true[1] , true[3] + true[1] 
                        ymin, ymax = true[4] - true[0] , true[4] + true[0]
                        width = true[0] *2
                        height = true[1] * 2
                        class_ = 'face'
                        file_name = lines[line][:-1]+ '.jpg'
                        data = {}
                        data['file_name'] = file_name
                        data['width'] = width
                        data['height'] = height
                        data["x_min"] = xmin   
                        data["y_min"] = ymin
                        data["x_max"] = xmax
                        data["y_max"] = ymax
                        data['class_name'] = 'face'
                        new_image[1].append(data)
                    folds[i_].append(new_image)

In [6]:
folds

{0: [[array([[[ 81, 117, 147],
           [ 82, 118, 148],
           [ 83, 120, 148],
           ...,
           [ 92, 129, 155],
           [ 92, 128, 158],
           [ 92, 128, 158]],
   
          [[ 81, 117, 147],
           [ 82, 118, 148],
           [ 84, 121, 149],
           ...,
           [ 92, 129, 155],
           [ 91, 127, 157],
           [ 91, 127, 157]],
   
          [[ 82, 118, 148],
           [ 83, 119, 149],
           [ 84, 121, 149],
           ...,
           [ 92, 129, 155],
           [ 90, 126, 156],
           [ 90, 126, 156]],
   
          ...,
   
          [[ 14,   6, 113],
           [ 10,   4, 111],
           [  8,   3, 108],
           ...,
           [ 32,  29,  24],
           [ 29,  25,  20],
           [ 30,  24,  19]],
   
          [[ 15,   7, 114],
           [ 13,   6, 111],
           [  9,   2, 106],
           ...,
           [ 31,  28,  23],
           [ 29,  25,  20],
           [ 30,  24,  19]],
   
          [[ 17,   7, 113],
     

In [4]:
VAL_FOLD = 0
dataset = ([folds[x] for x in folds if x != VAL_FOLD])

In [5]:
flatt = []
for x in dataset:
    flatt += x

In [6]:
len(flatt)

2555

In [7]:
def create_dataset_dicts(dataset):
  dataset_dicts = []
  for image_id, img in enumerate(dataset):
    record = {}
    image_df = img[0]
    file_path = img[1][0]['file_name']
    record["file_name"] = file_path
    record["image_id"] = image_id
    record["height"] = img[0].shape[0]
    record["width"] = img[0].shape[1]
    objs = []
    for row in img[1]:
      xmin = int(row['x_min'])
      ymin = int(row['y_min'])
      xmax = int(row['x_max'])
      ymax = int(row['y_max'])
      poly = [
          (xmin, ymin), (xmax, ymin),
          (xmax, ymax), (xmin, ymax)
      ]
      poly = list(itertools.chain.from_iterable(poly))
      obj = {
        "bbox": [xmin, ymin, xmax, ymax],
        "bbox_mode": BoxMode.XYXY_ABS,
        "segmentation": [poly],
        "category_id": 0,
        "iscrowd": 0
      }
      objs.append(obj)
    record["annotations"] = objs
    dataset_dicts.append(record)
  return dataset_dicts

classes = ['face']
for d in ["train", "val"]:
  DatasetCatalog.register("faces_" + d, lambda d=d: create_dataset_dicts(flatt if d == "train" else folds_[VAL_FOLD]))
  MetadataCatalog.get("faces_" + d).set(thing_classes=classes)
statement_metadata = MetadataCatalog.get("faces__train")

In [8]:
class CocoTrainer(DefaultTrainer):
  @classmethod
  def build_evaluator(cls, cfg, dataset_name, output_folder=None):
    if output_folder is None:
        os.makedirs("coco_eval", exist_ok=True)
        output_folder = "coco_eval"
    return COCOEvaluator(dataset_name, cfg, False, output_folder)

In [9]:
cfg = get_cfg()
cfg.merge_from_file(
  model_zoo.get_config_file(
    "COCO-InstanceSegmentation/mask_rcnn_X_101_32x8d_FPN_3x.yaml"
  )
)
cfg.MODEL.WEIGHTS = model_zoo.get_checkpoint_url(
  "COCO-InstanceSegmentation/mask_rcnn_X_101_32x8d_FPN_3x.yaml"
)

cfg.DATASETS.TRAIN = ("faces_train",)
cfg.DATASETS.TEST = ("faces_val",)
cfg.DATALOADER.NUM_WORKERS = 8
cfg.SOLVER.IMS_PER_BATCH = 2
cfg.SOLVER.BASE_LR = 0.001
cfg.SOLVER.WARMUP_ITERS = 1000
cfg.SOLVER.MAX_ITER = 2000
cfg.SOLVER.STEPS = (1000, 1500)
cfg.SOLVER.GAMMA = 0.05
cfg.MODEL.ROI_HEADS.BATCH_SIZE_PER_IMAGE = 32
cfg.MODEL.ROI_HEADS.NUM_CLASSES = len(classes)
cfg.TEST.EVAL_PERIOD = 500
os.makedirs(cfg.OUTPUT_DIR, exist_ok=True)
trainer = CocoTrainer(cfg)
trainer.resume_or_load(resume=False)
trainer.train()

[12/14 20:36:39 d2.engine.defaults]: Model:
GeneralizedRCNN(
  (backbone): FPN(
    (fpn_lateral2): Conv2d(256, 256, kernel_size=(1, 1), stride=(1, 1))
    (fpn_output2): Conv2d(256, 256, kernel_size=(3, 3), stride=(1, 1), padding=(1, 1))
    (fpn_lateral3): Conv2d(512, 256, kernel_size=(1, 1), stride=(1, 1))
    (fpn_output3): Conv2d(256, 256, kernel_size=(3, 3), stride=(1, 1), padding=(1, 1))
    (fpn_lateral4): Conv2d(1024, 256, kernel_size=(1, 1), stride=(1, 1))
    (fpn_output4): Conv2d(256, 256, kernel_size=(3, 3), stride=(1, 1), padding=(1, 1))
    (fpn_lateral5): Conv2d(2048, 256, kernel_size=(1, 1), stride=(1, 1))
    (fpn_output5): Conv2d(256, 256, kernel_size=(3, 3), stride=(1, 1), padding=(1, 1))
    (top_block): LastLevelMaxPool()
    (bottom_up): ResNet(
      (stem): BasicStem(
        (conv1): Conv2d(
          3, 64, kernel_size=(7, 7), stride=(2, 2), padding=(3, 3), bias=False
          (norm): FrozenBatchNorm2d(num_features=64, eps=1e-05)
        )
      )
      (res

Skip loading parameter 'roi_heads.box_predictor.cls_score.weight' to the model due to incompatible shapes: (81, 1024) in the checkpoint but (2, 1024) in the model! You might want to double check if this is expected.
Skip loading parameter 'roi_heads.box_predictor.cls_score.bias' to the model due to incompatible shapes: (81,) in the checkpoint but (2,) in the model! You might want to double check if this is expected.
Skip loading parameter 'roi_heads.box_predictor.bbox_pred.weight' to the model due to incompatible shapes: (320, 1024) in the checkpoint but (4, 1024) in the model! You might want to double check if this is expected.
Skip loading parameter 'roi_heads.box_predictor.bbox_pred.bias' to the model due to incompatible shapes: (320,) in the checkpoint but (4,) in the model! You might want to double check if this is expected.
Skip loading parameter 'roi_heads.mask_head.predictor.weight' to the model due to incompatible shapes: (80, 256, 1, 1) in the checkpoint but (1, 256, 1, 1) in

[12/14 20:36:39 d2.engine.train_loop]: Starting training from iteration 0
ERROR [12/14 20:36:55 d2.engine.train_loop]: Exception during training:
Traceback (most recent call last):
  File "c:\Users\Usuario\Desktop\Uni\DataDaniMAPSIV\PSIV\03-Tracking\detectron2_repo\detectron2\engine\train_loop.py", line 149, in train
    self.run_step()
  File "c:\Users\Usuario\Desktop\Uni\DataDaniMAPSIV\PSIV\03-Tracking\detectron2_repo\detectron2\engine\defaults.py", line 494, in run_step
    self._trainer.run_step()
  File "c:\Users\Usuario\Desktop\Uni\DataDaniMAPSIV\PSIV\03-Tracking\detectron2_repo\detectron2\engine\train_loop.py", line 273, in run_step
    loss_dict = self.model(data)
  File "C:\Users\Usuario\AppData\Local\Packages\PythonSoftwareFoundation.Python.3.9_qbz5n2kfra8p0\LocalCache\local-packages\Python39\site-packages\torch\nn\modules\module.py", line 1102, in _call_impl
    return forward_call(*input, **kwargs)
  File "c:\Users\Usuario\Desktop\Uni\DataDaniMAPSIV\PSIV\03-Tracking\detectr

RuntimeError: CUDA out of memory. Tried to allocate 22.00 MiB (GPU 0; 4.00 GiB total capacity; 2.12 GiB already allocated; 0 bytes free; 2.28 GiB reserved in total by PyTorch) If reserved memory is >> allocated memory try setting max_split_size_mb to avoid fragmentation.  See documentation for Memory Management and PYTORCH_CUDA_ALLOC_CONF

In [ ]:
!nvidia-smi

Tue Dec 14 20:32:23 2021       
+-----------------------------------------------------------------------------+
| NVIDIA-SMI 496.49       Driver Version: 496.49       CUDA Version: 11.5     |
|-------------------------------+----------------------+----------------------+
| GPU  Name            TCC/WDDM | Bus-Id        Disp.A | Volatile Uncorr. ECC |
| Fan  Temp  Perf  Pwr:Usage/Cap|         Memory-Usage | GPU-Util  Compute M. |
|                               |                      |               MIG M. |
|===============================+======================+======================|
|   0  NVIDIA GeForce ... WDDM  | 00000000:01:00.0 Off |                  N/A |
| N/A   56C    P0    14W /  N/A |    590MiB /  4096MiB |      0%      Default |
|                               |                      |                  N/A |
+-------------------------------+----------------------+----------------------+
                                                                               
+-------

In [17]:
!ps -aux

"ps" no se reconoce como un comando interno o externo,
programa o archivo por lotes ejecutable.
